In [1]:
from bs4 import BeautifulSoup
from pathlib import Path
from os.path import join
import urllib.request
import lxml
from functools import partial
from multiprocessing.dummy import Pool as ThreadPool
from tqdm import tqdm_notebook as tqdm
import pandas as pd
%reload_ext autoreload
%autoreload 2

In [92]:
fp_html = '/data_store/datasets/people/vgg_face/downloads/celeb_list.html'
with open(fp_html,'r') as fp:
  data = fp.readlines()
data = data[0]
#data = urllib.request.urlopen('https://www.youtube.com/watch?v=396sRuzVrHQ').read()

In [94]:
lines = data.split('<br>')

In [98]:
names = [x.split('&nbsp; ')[1].strip() for x in lines]

In [68]:

data_error2 = urllib.request.urlopen('https://www.youtube.com/watch?v=XAuCRa3ySfU').read()

In [70]:
soup = BeautifulSoup(data_error2, 'lxml')
desc_result = soup.find('p', attrs={'id': 'eow-description'})
if desc_result:
  print(desc_result.text)
else:
  print('no desc')

error_result = soup.find('div', attrs={'id': 'player-unavailable'})
if error_result:
  print(error_result.text)

no desc




              This video is unavailable.

    

Sorry about that.
    




In [71]:
data = """

    """

In [28]:
soup = BeautifulSoup(data, 'lxml')
d = soup.find('div', attrs={'id': 'description', 'slot': 'content'})
print(d.text)

If a recognizable person appears in this video, use for commercial purposes may infringe a right of privacy or publicity. It may not be used to state or imply the endorsement by NASA employees of a commercial product, process or service, or used in any other manner that might mislead. Accordingly, it is requested that if this video is used in advertising and other commercial promotion, layout and copy be submitted to NASA prior to release.


In [4]:
def parse_urls(url, exts):
  ahrefs = soup.find_all('img')
  urls = []
  for a in ahrefs:
    href = a['href']
    if Path(href).suffix[1:] in exts:
      urls.append('{}{}'.format(url, href))
  return urls

def parse_images(url, exts):
  imgs = soup.find_all('img')
  tags = []
  for img in imgs:
    src = img['src']
    if Path(src).suffix[1:] in exts:
      tags.append('{}{}'.format(url, src))
  return tags

metavars = [
  {'name': ('title','title')},
  {'name': ('description', 'description')},
  {'name': ('keywords', 'keywords')},
  {'itemprop': ('paid', 'paid')},
  {'itemprop': ('videoId', 'video_id')},
  {'itemprop': ('duration', 'duration')},
  {'itemprop': ('width', 'width')},
  {'itemprop': ('height', 'height')},
  {'itemprop': ('isFamilyFriendly', 'is_family_friendly')},
  {'itemprop': ('interactionCount', 'views')},
  {'itemprop': ('datePublished', 'date_published')},
  {'itemprop': ('genre', 'genre')},
  {'itemprop': ('unlisted', 'genre')}
]

def parse_yt_meta(soup, prop, propvals):
  content = soup.find('meta', attrs={prop:propvals[0]}).get('content','')
  return {propvals[1]: content}

def parse_yt_page(soup):
  #BeautifulSoup(data, 'html.parser').find(attrs={'name': 'description'})
  results = []
  for metavar in metavars:
    prop, propvals = list(metavar.items())[0]
    result = parse_yt_meta(soup, prop, propvals)
    #print(prop, propvals, result)
    results.append(result)
  return results

In [5]:
soup = BeautifulSoup(data,'lxml')
#burl = 'http://skuld.cs.umass.edu/traces/mmsys/2015/paper-5/devset/'
burl = ''
#tags = parse_urls(burl, ['jpg', 'txt'])
tags = parse_images(burl, ['jpg', 'png', 'gif'])
for t in tags:
  print(t)

# for row in rows:
#   ahrefs = row.find_all(href=True)
#   for a in ahrefs:
#     href = a['href']
#     if 'zip' in href:
#       url = 'http://{}'.format(Path(join(url_root, Path(href).name)))
#       print(url)

In [6]:
def get_papers(paper_id, sort_type='is-influential'):
  pages = 21
  results = []
  page_limit = 10
  num_pages = 2142 // page_limit
  num_pages = 990
  for page_num in range(num_pages):
    url = gen_url(paper_id, page_num, sort_type, page_limit=page_limit)
    print(f'get page {page_num}, {page_limit*page_num} - {(page_num+1)*page_limit}, for {url}')
    data = urllib.request.urlopen(url).read()
    soup = BeautifulSoup(data,'lxml')
    titles = soup.find_all('h2', attrs={'class': 'citation__title'})
    page_results = []
    for t in titles:
      page_results.append({'title': t.text, 'paper_id': t['data-heap-paper-id']})
    print(f'page contained {len(page_results)}')
    results += page_results
  print(len(results), 'return3ed results')
  return results

In [11]:
def gen_url(paper_id, page_num, sort_type, page_limit=10):
  url = 'https://www.semanticscholar.org/paper/'
  params = {
    'tab': 'abstract',
    'citingPapersSort': sort_type,  # citingPapersSort=year,is-influential
    'citingPapersLimit': page_limit,
    'citingPapersOffset': page_num * page_limit,
    'citedPapersSort': 'is-influential',
    'citedPapersLimit': 1,
    'citedPapersOffset': 0,
    }
  url_args = urllib.parse.urlencode(params)
  url = join(url, paper_id, f'?{url_args}')
  return url

def get_papers_mt(paper_id, sort_type='is-influential', opt_threads=4):
  
  def pool_process(url_obj):
    # threaded function
    results = []
    try:
      #print(f'get page {page_num}, {page_limit*page_num} - {(page_num+1)*page_limit}, for {url}')
      data = urllib.request.urlopen(url_obj['url'], timeout=30).read()
      soup = BeautifulSoup(data,'lxml')
      titles = soup.find_all('h2', attrs={'class': 'citation__title'})
      page_results = []
      for t in titles:
        page_results.append({'title': t.text, 'paper_id': t['data-heap-paper-id']})
      results += page_results
    except Exception as e:
      print(f'Error: {e}, {url_obj["url"]}')
    pbar.update(1)
    return results  # list of paper title and id

  # pregenerate URLs
  page_limit = 10
  num_pages = 990 // page_limit
  url_objs = []
  for page_num in range(num_pages):
    url = gen_url(paper_id, page_num, sort_type, page_limit=page_limit)
    url_objs.append({'url': url, 'sort_type':sort_type})

  results = []
  opt_threads = 20
  pbar = tqdm(total=len(url_objs))
  pool_process = partial(pool_process)
  pool = ThreadPool(opt_threads) 
  with tqdm(total=len(url_objs)) as pbar:
    results = pool.map(pool_process, url_objs)
            
  pbar.close()
  return results

In [15]:
paper_id = '370b5757a5379b15e30d619e4d3fb9e8e13f3256'
papers_influ = get_papers_mt(paper_id, sort_type='is-influential', opt_threads=4)

In [17]:
papers_year = get_papers_mt(paper_id, sort_type='year', opt_threads=4)

In [ ]:
papers_all = []
for pl in papers_influ:
  for p in pl:
    papers_

In [21]:
papers_all = []
papers_ids  = []
for paper_list in papers_influ:
  for paper in paper_list:
    paper_id = paper['paper_id']
    if not paper_id in papers_ids:
      papers_ids.append(paper_id)
      papers_all.append(p)
for paper_list in papers_year:
  for paper in paper_list:
    paper_id = paper['paper_id']
    if not paper_id in papers_ids:
      papers_ids.append(paper_id)
      papers_all.append(p)

In [22]:
print(len(papers_all))

1317
